This code demos how to Read output files for the ICESat-2 satellite that have already been turned into cleaned pickle files. Each pickle contains a months worth of daily model densities (for the 4 empirical models), scaling factors, and residuals.

This notebook then demonstrates how to extract the scaling factors, scaled model densities, and weighted average of the scaled densities from the data and visualizes it. 

# Imports and book keeping

In [1]:
from pygeodyn.PYGEODYN import Pygeodyn
import datetime

scaling_cadence = 3
scale_cadence = scaling_cadence
index_buffarc_start = 0
run_list = [
                'msis2',
                'jb2008',
                'dtm2020_o',
                'hasdm_oc'
           ]

year_list = [2018,2019]
month_list = ['jan', 'feb', 'mar', 'apr','may', 'jun','jul','aug','sep', 'oct', 'nov','dec' ]


dir_modeldat='/data/SatDragModelValidation/data/inputs/atmos_models'
run_dict={}
for i in run_list:
    for y_num in year_list: #, 
        for imonth,month in enumerate(month_list):
            if y_num==2018 and month not in ['oct', 'nov', 'dec']:
                print(f'Skipping {y_num}.{month}')
                continue

            if i =='msis2':
                run_dict[str(y_num)+month+i]={}
                run_dict[str(y_num)+month+i]['num'] = 5
                run_dict[str(y_num)+month+i]['model_path'] = None
            if i =='dtm2020_o':
                run_dict[str(y_num)+month+i]={}
                run_dict[str(y_num)+month+i]['num'] = 3
                run_dict[str(y_num)+month+i]['model_path'] = None
            if i =='jb2008':
                run_dict[str(y_num)+month+i]={}
                run_dict[str(y_num)+month+i]['num'] = 1
                run_dict[str(y_num)+month+i]['model_path'] = None
            if i =='hasdm_oc':
                run_dict[str(y_num)+month+i]={}
                run_dict[str(y_num)+month+i]['num'] = 2 
                run_dict[str(y_num)+month+i]['model_path'] = dir_modeldat+'/hasdm/sethasdm_orbitclouds' #HASDM_OrbitCloud_2018313.01.csv


print(run_dict)

Skipping 2018.jan
Skipping 2018.feb
Skipping 2018.mar
Skipping 2018.apr
Skipping 2018.may
Skipping 2018.jun
Skipping 2018.jul
Skipping 2018.aug
Skipping 2018.sep
Skipping 2018.jan
Skipping 2018.feb
Skipping 2018.mar
Skipping 2018.apr
Skipping 2018.may
Skipping 2018.jun
Skipping 2018.jul
Skipping 2018.aug
Skipping 2018.sep
Skipping 2018.jan
Skipping 2018.feb
Skipping 2018.mar
Skipping 2018.apr
Skipping 2018.may
Skipping 2018.jun
Skipping 2018.jul
Skipping 2018.aug
Skipping 2018.sep
Skipping 2018.jan
Skipping 2018.feb
Skipping 2018.mar
Skipping 2018.apr
Skipping 2018.may
Skipping 2018.jun
Skipping 2018.jul
Skipping 2018.aug
Skipping 2018.sep
{'2018octmsis2': {'num': 5, 'model_path': None}, '2018novmsis2': {'num': 5, 'model_path': None}, '2018decmsis2': {'num': 5, 'model_path': None}, '2019janmsis2': {'num': 5, 'model_path': None}, '2019febmsis2': {'num': 5, 'model_path': None}, '2019marmsis2': {'num': 5, 'model_path': None}, '2019aprmsis2': {'num': 5, 'model_path': None}, '2019maymsis2':

# Prep and Check Arcs and times

In [2]:
import pandas as pd
from datetime import datetime,timedelta
import numpy as np



arc_timesfile = '/data/SatDragModelValidation/data/inputs/raw_inputdata/data_ICESat2/arc_times.txt'

### Make a function that finds the right range of dates in this file.
arcs = pd.read_csv(arc_timesfile, 
            sep = ',',
#             dtype=object,
            names = [
                'arc'         ,
                'epoch_start' ,
                'epoch_stop'  ,
                'orbit_start' ,
                'orbit_stop'  ,
                    ],)


arcs_yyyyddd = [x.strip() for x in arcs['arc'].values.tolist()]
epochstart   = [x.strip() for x in arcs['orbit_start'].values.tolist()]
epochstop    = [x.strip() for x in arcs['orbit_stop' ].values.tolist()]


input_arcs       = []
input_epochstart = []
input_epochstop  = []
arc_length = []
scaleparameter_times = []

for y_num in year_list:

    for imonth,month in enumerate(month_list):
        if month=='jan':  m_num = 1
        if month=='feb':  m_num = 2
        if month=='mar':  m_num = 3
        if month=='apr':  m_num = 4
        if month=='may':  m_num = 5
        if month=='jun':  m_num = 6
        if month=='jul':  m_num = 7
        if month=='aug':  m_num = 8
        if month=='sep':  m_num = 9
        if month=='oct':  m_num = 10
        if month=='nov':  m_num = 11
        if month=='dec':  m_num = 12




        for i,val in enumerate(arcs_yyyyddd):

            if pd.to_datetime(val[:8],format="%Y.%j").month == m_num and pd.to_datetime(val[:8],format="%Y.%j").year == y_num:
                epoch_delta  =  pd.to_timedelta(pd.to_datetime(epochstop[i]) - pd.to_datetime(epochstart[i]), 'hours')
                arc_length.append(epoch_delta.total_seconds()/3600)

                if val[8:] == 'A' or val[8:] == 'B':
                    input_arcs.append(      arcs_yyyyddd[i])
                    input_epochstart.append(epochstart[i])
                    input_epochstop.append( epochstop[i])
    #                 scaleparameter_times.append(dict_sftime[arcs_yyyyddd[i]])
                    scalestart = str(pd.to_datetime(arcs_yyyyddd[i][:-1],format="%Y.%j"))
                    scalestop  = str(pd.to_datetime(arcs_yyyyddd[i][:-1],format="%Y.%j") + pd.to_timedelta(24,'h'))
                    scaletimes = pd.date_range(start = pd.to_datetime(scalestart),
                                                              end   = pd.to_datetime( epochstop[i] ),
                                                              freq=str(scale_cadence)+"h")
                    
                    if epochstop[i] in scaletimes:  ## dont add repeats to the final epoch time
                        ### Append the epoch end time to the end
                        add_epochend = scaletimes.values.astype(np.int64) // 10 ** 9
                                        #np.append(scaletimes.values.astype(np.int64) // 10 ** 9,
                                      #pd.to_datetime(pd.Series(epochstop[i])).values.astype(np.int64) // 10 ** 9)

                        scaleparameter_times.append([pd.to_datetime(datetime.strftime(datetime.fromtimestamp(ts), '%y%m%d%H%M%S.%f'),
                            format ='%y%m%d%H%M%S.%f' )
                                         for ts in add_epochend  ])


                    else:
                        ### Append the epoch end time to the end
                        add_epochend = np.append(scaletimes.values.astype(np.int64) // 10 ** 9,
                                      pd.to_datetime(pd.Series(epochstop[i])).values.astype(np.int64) // 10 ** 9)


                        scaleparameter_times.append([pd.to_datetime(datetime.strftime(datetime.fromtimestamp(ts), '%y%m%d%H%M%S.%f'),
                            format ='%y%m%d%H%M%S.%f' )
                                         for ts in add_epochend  ])

                    pass
                else:

                    ### Use Arc text file times
                    input_arcs.append(      arcs_yyyyddd[i])
                    input_epochstart.append(epochstart[i])
                    input_epochstop.append( epochstop[i])
    #                 print(f"epoch_top {epochstop[i]}")
                    scalestart = str(pd.to_datetime(arcs_yyyyddd[i],format="%Y.%j"))
                    scalestop  = str(pd.to_datetime(arcs_yyyyddd[i],format="%Y.%j") + pd.to_timedelta(24,'h'))
                    scaletimes = pd.date_range(start = pd.to_datetime(scalestart),
                                                              end   = pd.to_datetime(scalestop ),
                                                              freq=str(scale_cadence)+"h")

                    ### Append the epoch end time to the end
                    add_epochend = np.append(scaletimes.values.astype(np.int64) // 10 ** 9,
                                  pd.to_datetime(pd.Series(epochstop[i])).values.astype(np.int64) // 10 ** 9)


                    scaleparameter_times.append([pd.to_datetime(datetime.strftime(datetime.fromtimestamp(ts), '%y%m%d%H%M%S.%f'),
                        format ='%y%m%d%H%M%S.%f' )
                                     for ts in add_epochend ])
for i,val in enumerate(input_arcs):
    print(f" {input_arcs[i]:10}  , {input_epochstart[i]:20},  {input_epochstop[i]:20}, {arc_length[i]}")
#     if val[8:] == 'A' or val[8:] == 'B':
    print(f" {'':10}  , {scaleparameter_times[i]}")
    print("") 



 2018.288    , 2018-10-14 21:18:00 ,  2018-10-16 02:42:00 , 29.4
             , [Timestamp('2018-10-15 00:00:00'), Timestamp('2018-10-15 03:00:00'), Timestamp('2018-10-15 06:00:00'), Timestamp('2018-10-15 09:00:00'), Timestamp('2018-10-15 12:00:00'), Timestamp('2018-10-15 15:00:00'), Timestamp('2018-10-15 18:00:00'), Timestamp('2018-10-15 21:00:00'), Timestamp('2018-10-16 00:00:00'), Timestamp('2018-10-16 02:42:00')]

 2018.289A   , 2018-10-15 21:18:00 ,  2018-10-16 23:00:00 , 25.7
             , [Timestamp('2018-10-16 00:00:00'), Timestamp('2018-10-16 03:00:00'), Timestamp('2018-10-16 06:00:00'), Timestamp('2018-10-16 09:00:00'), Timestamp('2018-10-16 12:00:00'), Timestamp('2018-10-16 15:00:00'), Timestamp('2018-10-16 18:00:00'), Timestamp('2018-10-16 21:00:00'), Timestamp('2018-10-16 23:00:00')]

 2018.290A   , 2018-10-17 00:24:00 ,  2018-10-18 02:42:00 , 26.3
             , [Timestamp('2018-10-17 00:00:00'), Timestamp('2018-10-17 03:00:00'), Timestamp('2018-10-17 06:00:00'), Timesta

# GEODYN Run Settings

In [3]:
def setsettings(den, y_num, month, run_dict, scaling_cadence, file_raw_ICs, file_g2b, input_arcs, input_epochstart, input_epochstop, scaleparameter_times):
    
    settings_ice= {# Basic input settings
                 'satellite'      : {'input': 'icesat2'},
                 'den_model'      : {'input': den},
                 'run_type'       : {'input': 'DataReduction_PCE'},
                 'run_specifier'  : {'input': '_'+str(y_num)+month},
                 'cd_model'       : {'input': 'DRIA'},
                 'file_string'    : {'input': 'DRIAscaled_'},
                 'model_data_path' : {'input': run_dict[str(y_num)+month+den]['model_path']},
                 # Force Model settings
                  'scaling_factor'        : {'input':True},
                  'cd_value'              : {'input':1.0 },
                  'hours_between_cd_adj'  : {'input':scaling_cadence},
                  #### Comment for unadjusted run:
                  'cd_adjustment_boolean' : {'input':True },
                #### DRIA CD Model Parameters
                'cd_model_params' : {'input':{ 
                        'MS'     : '26.980D0'   ,  #!  molar mass for each panel (g/mol)
                        'TW'     : '300.0D0'    ,  #!  temperature of panels  (K)
                           ###  Alpha is b/w 0 and 1
                        'ALPHA'  : '0.890D0'    ,  #!  accomodation coefficient
                        'KL'     : '0.0D0'    ,    #!  langmuir parameter
                        'FRACOX' : '1.0D0'   ,     #!  fraction of surface covered by atomic oxygen
                   }},
                  #### ---------------------------------------
                 # Run
                  'arc_type'       : {'input':'Nominal30hr_and_AB'},      
                  'step'           : {'input': 10},
                  'orbfil_step'    : {'input': 120.},
                  'which_ICfile'   : {'input':file_raw_ICs},
                  'which_g2bfile'  : {'input':file_g2b},
                    #
                  'arc'            : {'input': input_arcs},
                  'epoch_start'    : {'input': input_epochstart},
                  'epoch_stop'     : {'input': input_epochstop},  
            'scaleparameter_times' : {'input': scaleparameter_times},  
                   #                                
                  'global_options' : {'input':'pso_2018'},
                 # Request read on raw outputs
                  'request_data'   : {'input': ['Trajectory_orbfil', 
                                               'Density', 
                                               'Residuals_summary',
                                               'DragFile',
                                               'AdjustedParams'
                                               ]},
              #end dict
              }
    return(settings_ice)


# Read GEODYN Monthly outputs

In [4]:
%load_ext autoreload
%autoreload 2
from gc import collect as gc_collect
import pickle 
import os
from datetime import datetime,timedelta


g2b_path = "/data/SatDragModelValidation/data/inputs/sat_icesat2/g2b/"

dir_save    =  '/data/SatDragModelValidation/data/outputs_clean/'\
             + 'icesat2/FinalDatasets_SWJ2025/'

obj = {}

for y_num in year_list: #

    for imonth,month in enumerate(month_list):
        if month=='jan':  m_num = 1
        if month=='feb':  m_num = 2
        if month=='mar':  m_num = 3
        if month=='apr':  m_num = 4
        if month=='may':  m_num = 5
        if month=='jun':  m_num = 6
        if month=='jul':  m_num = 7
        if month=='aug':  m_num = 8
        if month=='sep':  m_num = 9
        if month=='oct':  m_num = 10
        if month=='nov':  m_num = 11
        if month=='dec':  m_num = 12
            
        if y_num==2018 and m_num<10:
            print(f'Skipping {y_num}.{m_num}')
            continue
                        
        file_raw_ICs = f"{g2b_path}ICESat2_RawEphem_{y_num}_{m_num:02d}.txt"
        file_g2b     = f"pce_icesat2_pso_{y_num}_{m_num:02d}"

        input_arcs           = []
        input_epochstart     = []
        input_epochstop      = []
        arc_length           = []
        scaleparameter_times = []

        for i,val in enumerate(arcs_yyyyddd):


            if pd.to_datetime(val[:8],format="%Y.%j").month == m_num and pd.to_datetime(val[:8],format="%Y.%j").year == y_num:
                epoch_delta  =  pd.to_timedelta(pd.to_datetime(epochstop[i]) - pd.to_datetime(epochstart[i]), 'hours')
                arc_length.append(epoch_delta.total_seconds()/3600)

                if val[8:] == 'A' or val[8:] == 'B':
                    input_arcs.append(      arcs_yyyyddd[i])
                    input_epochstart.append(epochstart[i])
                    input_epochstop.append( epochstop[i])
                    scalestart = str(pd.to_datetime(arcs_yyyyddd[i][:-1],format="%Y.%j"))
                    scalestop  = str(pd.to_datetime(arcs_yyyyddd[i][:-1],format="%Y.%j") + pd.to_timedelta(24,'h'))
                    scaletimes = pd.date_range(start = pd.to_datetime(scalestart),
                                                              end   = pd.to_datetime( epochstop[i] ),
                                                              freq=str(scale_cadence)+"h")
                
                    if epochstop[i] in scaletimes:  ## dont add repeats to the final epoch time
                        ### Append the epoch end time to the end
                        add_epochend = scaletimes.values.astype(np.int64) // 10 ** 9
                                        #np.append(scaletimes.values.astype(np.int64) // 10 ** 9,
                                      #pd.to_datetime(pd.Series(epochstop[i])).values.astype(np.int64) // 10 ** 9)

                        scaleparameter_times.append([pd.to_datetime(datetime.strftime(datetime.fromtimestamp(ts), '%y%m%d%H%M%S.%f'),
                            format ='%y%m%d%H%M%S.%f' )
                                         for ts in add_epochend  ])
                    else:
                        ### Append the epoch end time to the end
                        add_epochend = np.append(scaletimes.values.astype(np.int64) // 10 ** 9,
                                      pd.to_datetime(pd.Series(epochstop[i])).values.astype(np.int64) // 10 ** 9)


                        scaleparameter_times.append([pd.to_datetime(datetime.strftime(datetime.fromtimestamp(ts), '%y%m%d%H%M%S.%f'),
                            format ='%y%m%d%H%M%S.%f' )
                                         for ts in add_epochend ])
                else:

                    ### Use Arc text file times
                    input_arcs.append(      arcs_yyyyddd[i])
                    input_epochstart.append(epochstart[i])
                    input_epochstop.append( epochstop[i])
    #                 print(f"epoch_top {epochstop[i]}")
                    scalestart = str(pd.to_datetime(arcs_yyyyddd[i],format="%Y.%j"))
                    scalestop  = str(pd.to_datetime(arcs_yyyyddd[i],format="%Y.%j") + pd.to_timedelta(24,'h'))
                    scaletimes = pd.date_range(start = pd.to_datetime(scalestart),
                                                              end   = pd.to_datetime(scalestop ),
                                                              freq=str(scale_cadence)+"h")

                    ### Append the epoch end time to the end
                    add_epochend = np.append(scaletimes.values.astype(np.int64) // 10 ** 9,
                                  pd.to_datetime(pd.Series(epochstop[i])).values.astype(np.int64) // 10 ** 9)


                    scaleparameter_times.append([pd.to_datetime(datetime.strftime(datetime.fromtimestamp(ts), '%y%m%d%H%M%S.%f'),
                        format ='%y%m%d%H%M%S.%f' )
                                     for ts in add_epochend ])

        for i,val in enumerate(input_arcs):
            print(f" {input_arcs[i]:10}  , {input_epochstart[i]:20},  {input_epochstop[i]:20}, {arc_length[i]}")
            if val[8:] == 'A' or val[8:] == 'B':
                print(f" {'':10}  , {scaleparameter_times[i]}")
                print("")

            else:
        #         print(f" {'':10}  , {scaleparameter_times[i]}")
                print("")     
    
#         ##### ----------------------------------------------------------------------------------------------------
#         ##### RUN GEODYN for desired Arcs
#         ##### ----------------------------
#         for i,den in enumerate(run_list):
#             if y_num == 2019 and month in ['jan','feb', 'mar','apr', 'may','jun','jul','aug','sep','oct','nov'] :
#                 print(f"already ran {month} for {den}")

#             elif y_num == 2019 and month == 'dec' and den in ['msis2', 'jb2008','dtm2020_o']:
#                 print(f"already ran {month} for {den}")
            
#             elif y_num == 2019 and month == 'dec' and den == 'hasdm_oc':
                
#                 input_arcs           = input_arcs[:-1]
#                 input_epochstart     = input_epochstart[:-1]
#                 input_epochstop      = input_epochstop[:-1]
#                 scaleparameter_times = scaleparameter_times[:-1]
                
#                 settings_ice = setsettings(den, y_num, month, run_dict, scaling_cadence, file_raw_ICs, file_g2b, 
#                                              input_arcs, 
#                                              input_epochstart, 
#                                              input_epochstop, 
#                                              scaleparameter_times)

#                 sat = Pygeodyn(settings_ice, use_file=False)
#                 sat.run_arcs()

#             else:                
#                 settings_ice = setsettings(den, y_num, month, run_dict, scaling_cadence, file_raw_ICs, file_g2b, 
#                                              input_arcs, 
#                                              input_epochstart, 
#                                              input_epochstop, 
#                                              scaleparameter_times)

#                 sat = Pygeodyn(settings_ice, use_file=False)
#                 sat.run_arcs()
#         ##### End Run GEODYN        
#         ##### ----------------------------------------------------------------------------------------------------

          
        ##### ----------------------------------------------------------------------------------------------------
        #### READ GEODYN OUTPUTS
        ##### --------------------
        for i,den in enumerate(run_list):
            
            if y_num==2018 and month not in ['oct', 'nov', 'dec']:
                print(f'Skipping {y_num}.{month}')
                                
            elif y_num == 2019 and month == 'dec':
                
                input_arcs           = input_arcs[:-1]
                input_epochstart     = input_epochstart[:-1]
                input_epochstop      = input_epochstop[:-1]
                scaleparameter_times = scaleparameter_times[:-1]
                
                settings_ice = setsettings(den, y_num, month, run_dict, scaling_cadence, file_raw_ICs, file_g2b, 
                                             input_arcs, 
                                             input_epochstart, 
                                             input_epochstop, 
                                             scaleparameter_times)
                sat = Pygeodyn(settings_ice, use_file=False)

            else:
                settings_ice = setsettings(den,y_num, month, run_dict, scaling_cadence, file_raw_ICs, file_g2b, 
                                             input_arcs, 
                                             input_epochstart, 
                                             input_epochstop, 
                                             scaleparameter_times)
                
                sat = Pygeodyn(settings_ice, use_file=False)
#             obj[str(y_num)+month+den] =  sat.getData_BigData_lowmemory(orbit_propagation=False)
#             obj[str(y_num)+month+den] = vars(obj[str(y_num)+month+den])
#             gc_collect()


            pickleName = f'_{y_num}.{month}_DRIA_scale{scale_cadence}.pkl'

            pickle_file = dir_save+den+pickleName
            if not os.path.exists(pickle_file):
                print('Must create pickle file...')
                print('   ',  pickle_file)
                print('   ', 'Reading Geodyn Data')

                ### Load the data into an object
                sat = Pygeodyn(settings_ice, use_file=False)
                obj = sat.getData_BigData_lowmemory(orbit_propagation=False)
                gc_collect()

                #### Pickle the object to save it
                print('   ', 'Saving pickle')
                filehandler = open(pickle_file, 'wb') 
                pickle.dump(vars(obj), filehandler)
                filehandler.close()
                obj = 0
                print('   ', 'Saved pickle')

    for i,model in enumerate(run_list):
#         print('RUNLIST',model)
        for imonth,month in enumerate(month_list):
            
            print('y_num month',y_num, month)
            if y_num==2018 and month not in ['oct', 'nov', 'dec']:
                print(f'Skipping {y_num}.{month}')
                
#             elif y_num==2019 and month in ['jan', 'feb', 'mar', 'apr']:
#                 print(f'Skipping {y_num}.{month}')
                
            else:
                pickleName = f'_{y_num}.{month}_DRIA_scale{scale_cadence}.pkl'

                ### Load the data if the pickles exist
                print()
                print()
                gc_collect()

                pickle_file = dir_save+model+pickleName

                obj[str(y_num)+month+model] = pd.read_pickle(pickle_file)
        #         filehandler = open(pickle_file, 'rb') 
        #         obj[month+model] = pickle.load(filehandler)
        #         filehandler.close()
                print('Loaded data from pickle... ',y_num, month, model)

### Save space if doing density retrieval
for model in run_dict.keys():
    print(model)
    del obj[model]['OrbitResids']
    del obj[model]['Trajectory_orbfil']

gc_collect()

Skipping 2018.1
Skipping 2018.2
Skipping 2018.3
Skipping 2018.4
Skipping 2018.5
Skipping 2018.6
Skipping 2018.7
Skipping 2018.8
Skipping 2018.9
 2018.288    , 2018-10-14 21:18:00 ,  2018-10-16 02:42:00 , 29.4

 2018.289A   , 2018-10-15 21:18:00 ,  2018-10-16 23:00:00 , 25.7
             , [Timestamp('2018-10-16 00:00:00'), Timestamp('2018-10-16 03:00:00'), Timestamp('2018-10-16 06:00:00'), Timestamp('2018-10-16 09:00:00'), Timestamp('2018-10-16 12:00:00'), Timestamp('2018-10-16 15:00:00'), Timestamp('2018-10-16 18:00:00'), Timestamp('2018-10-16 21:00:00'), Timestamp('2018-10-16 23:00:00')]

 2018.290A   , 2018-10-17 00:24:00 ,  2018-10-18 02:42:00 , 26.3
             , [Timestamp('2018-10-17 00:00:00'), Timestamp('2018-10-17 03:00:00'), Timestamp('2018-10-17 06:00:00'), Timestamp('2018-10-17 09:00:00'), Timestamp('2018-10-17 12:00:00'), Timestamp('2018-10-17 15:00:00'), Timestamp('2018-10-17 18:00:00'), Timestamp('2018-10-17 21:00:00'), Timestamp('2018-10-18 00:00:00'), Timestamp('2018

 2018.335    , 2018-11-30 21:18:00 ,  2018-12-02 02:42:00 , 29.4

 2018.336    , 2018-12-01 21:18:00 ,  2018-12-03 02:42:00 , 29.4

 2018.337    , 2018-12-02 21:18:00 ,  2018-12-04 02:42:00 , 29.4

 2018.338    , 2018-12-03 21:18:00 ,  2018-12-05 02:42:00 , 29.4

 2018.339A   , 2018-12-04 21:18:00 ,  2018-12-05 13:58:00 , 16.666666666666668
             , [Timestamp('2018-12-05 00:00:00'), Timestamp('2018-12-05 03:00:00'), Timestamp('2018-12-05 06:00:00'), Timestamp('2018-12-05 09:00:00'), Timestamp('2018-12-05 12:00:00'), Timestamp('2018-12-05 13:58:00')]

 2018.340A   , 2018-12-05 22:22:00 ,  2018-12-06 14:30:00 , 16.133333333333333
             , [Timestamp('2018-12-06 00:00:00'), Timestamp('2018-12-06 03:00:00'), Timestamp('2018-12-06 06:00:00'), Timestamp('2018-12-06 09:00:00'), Timestamp('2018-12-06 12:00:00'), Timestamp('2018-12-06 14:30:00')]

 2018.340B   , 2018-12-06 16:54:00 ,  2018-12-07 02:42:00 , 9.8
             , [Timestamp('2018-12-06 00:00:00'), Timestamp('2018-12-06 

Loaded data from pickle...  2018 nov msis2
y_num month 2018 dec


Loaded data from pickle...  2018 dec msis2
y_num month 2018 jan
Skipping 2018.jan
y_num month 2018 feb
Skipping 2018.feb
y_num month 2018 mar
Skipping 2018.mar
y_num month 2018 apr
Skipping 2018.apr
y_num month 2018 may
Skipping 2018.may
y_num month 2018 jun
Skipping 2018.jun
y_num month 2018 jul
Skipping 2018.jul
y_num month 2018 aug
Skipping 2018.aug
y_num month 2018 sep
Skipping 2018.sep
y_num month 2018 oct


Loaded data from pickle...  2018 oct jb2008
y_num month 2018 nov


Loaded data from pickle...  2018 nov jb2008
y_num month 2018 dec


Loaded data from pickle...  2018 dec jb2008
y_num month 2018 jan
Skipping 2018.jan
y_num month 2018 feb
Skipping 2018.feb
y_num month 2018 mar
Skipping 2018.mar
y_num month 2018 apr
Skipping 2018.apr
y_num month 2018 may
Skipping 2018.may
y_num month 2018 jun
Skipping 2018.jun
y_num month 2018 jul
Skipping 2018.jul
y_num month 2018 aug
Skipping 2018.aug
y_num month 2018 sep
Skippi

 2019.032    , 2019-01-31 21:18:00 ,  2019-02-02 02:42:00 , 29.4

 2019.033    , 2019-02-01 21:18:00 ,  2019-02-03 02:42:00 , 29.4

 2019.034    , 2019-02-02 21:18:00 ,  2019-02-04 02:42:00 , 29.4

 2019.035    , 2019-02-03 21:18:00 ,  2019-02-05 02:42:00 , 29.4

 2019.036    , 2019-02-04 21:18:00 ,  2019-02-06 02:42:00 , 29.4

 2019.037    , 2019-02-05 21:18:00 ,  2019-02-07 02:42:00 , 29.4

 2019.038    , 2019-02-06 21:18:00 ,  2019-02-08 02:42:00 , 29.4

 2019.039    , 2019-02-07 21:18:00 ,  2019-02-09 02:42:00 , 29.4

 2019.040    , 2019-02-08 21:18:00 ,  2019-02-10 02:42:00 , 29.4

 2019.041    , 2019-02-09 21:18:00 ,  2019-02-11 02:42:00 , 29.4

 2019.042A   , 2019-02-10 21:18:00 ,  2019-02-12 00:48:00 , 27.5
             , [Timestamp('2019-02-11 00:00:00'), Timestamp('2019-02-11 03:00:00'), Timestamp('2019-02-11 06:00:00'), Timestamp('2019-02-11 09:00:00'), Timestamp('2019-02-11 12:00:00'), Timestamp('2019-02-11 15:00:00'), Timestamp('2019-02-11 18:00:00'), Timestamp('2019-02-11

 2019.091A   , 2019-03-31 21:18:00 ,  2019-04-01 19:42:00 , 22.4
             , [Timestamp('2019-04-01 00:00:00'), Timestamp('2019-04-01 03:00:00'), Timestamp('2019-04-01 06:00:00'), Timestamp('2019-04-01 09:00:00'), Timestamp('2019-04-01 12:00:00'), Timestamp('2019-04-01 15:00:00'), Timestamp('2019-04-01 18:00:00'), Timestamp('2019-04-01 19:42:00')]

 2019.092A   , 2019-04-01 21:30:00 ,  2019-04-03 02:42:00 , 29.2
             , [Timestamp('2019-04-02 00:00:00'), Timestamp('2019-04-02 03:00:00'), Timestamp('2019-04-02 06:00:00'), Timestamp('2019-04-02 09:00:00'), Timestamp('2019-04-02 12:00:00'), Timestamp('2019-04-02 15:00:00'), Timestamp('2019-04-02 18:00:00'), Timestamp('2019-04-02 21:00:00'), Timestamp('2019-04-03 00:00:00'), Timestamp('2019-04-03 02:42:00')]

 2019.093    , 2019-04-02 21:18:00 ,  2019-04-04 02:42:00 , 29.4

 2019.094    , 2019-04-03 21:18:00 ,  2019-04-05 02:42:00 , 29.4

 2019.095    , 2019-04-04 21:18:00 ,  2019-04-06 02:42:00 , 29.4

 2019.096    , 2019-04-05 

...

 2019.213    , 2019-07-31 21:18:00 ,  2019-08-02 02:42:00 , 29.4

 2019.214    , 2019-08-01 21:18:00 ,  2019-08-03 02:42:00 , 29.4

 2019.215    , 2019-08-02 21:18:00 ,  2019-08-04 02:42:00 , 29.4

 2019.216    , 2019-08-03 21:18:00 ,  2019-08-05 02:42:00 , 29.4

 2019.217    , 2019-08-04 21:18:00 ,  2019-08-06 02:42:00 , 29.4

 2019.218    , 2019-08-05 21:18:00 ,  2019-08-07 02:42:00 , 29.4

 2019.219    , 2019-08-06 21:18:00 ,  2019-08-08 02:42:00 , 29.4

 2019.220A   , 2019-08-07 21:18:00 ,  2019-08-09 01:48:00 , 28.5
             , [Timestamp('2019-08-08 00:00:00'), Timestamp('2019-08-08 03:00:00'), Timestamp('2019-08-08 06:00:00'), Timestamp('2019-08-08 09:00:00'), Timestamp('2019-08-08 12:00:00'), Timestamp('2019-08-08 15:00:00'), Timestamp('2019-08-08 18:00:00'), Timestamp('2019-08-08 21:00:00'), Timestamp('2019-08-09 00:00:00'), Timestamp('2019-08-09 01:48:00')]

 2019.221A   , 2019-08-09 03:30:00 ,  2019-08-10 02:42:00 , 23.2
             , [Timestamp('2019-08-09 00:00:00'), T

Using the ICESat-2 Class
['2019-08-31 21:18:00', '2019-09-01 21:18:00', '2019-09-02 21:18:00', '2019-09-03 21:18:00', '2019-09-05 02:18:00', '2019-09-05 21:18:00', '2019-09-07 01:36:00', '2019-09-07 21:18:00', '2019-09-08 21:18:00', '2019-09-09 21:18:00', '2019-09-10 21:18:00', '2019-09-11 21:18:00', '2019-09-13 01:00:00', '2019-09-13 21:18:00', '2019-09-14 21:18:00', '2019-09-15 21:18:00', '2019-09-16 21:18:00', '2019-09-17 21:18:00', '2019-09-18 21:18:00', '2019-09-19 13:24:00', '2019-09-19 21:18:00', '2019-09-20 21:18:00', '2019-09-21 21:18:00', '2019-09-22 21:18:00', '2019-09-23 21:18:00', '2019-09-24 21:18:00', '2019-09-25 21:18:00', '2019-09-26 21:18:00', '2019-09-27 21:18:00', '2019-09-28 21:18:00', '2019-09-29 21:18:00', '2019-09-30 14:30:00']
check sat ICESat2
 2019.274    , 2019-09-30 21:18:00 ,  2019-10-02 02:42:00 , 29.4

 2019.275    , 2019-10-01 21:18:00 ,  2019-10-03 02:42:00 , 29.4

 2019.276    , 2019-10-02 21:18:00 ,  2019-10-04 02:42:00 , 29.4

 2019.277    , 2019-10

 2019.305    , 2019-10-31 21:18:00 ,  2019-11-02 02:42:00 , 29.4

 2019.306A   , 2019-11-01 21:18:00 ,  2019-11-02 12:54:00 , 15.6
             , [Timestamp('2019-11-02 00:00:00'), Timestamp('2019-11-02 03:00:00'), Timestamp('2019-11-02 06:00:00'), Timestamp('2019-11-02 09:00:00'), Timestamp('2019-11-02 12:00:00'), Timestamp('2019-11-02 12:54:00')]

 2019.306B   , 2019-11-02 14:12:00 ,  2019-11-03 02:42:00 , 12.5
             , [Timestamp('2019-11-02 00:00:00'), Timestamp('2019-11-02 03:00:00'), Timestamp('2019-11-02 06:00:00'), Timestamp('2019-11-02 09:00:00'), Timestamp('2019-11-02 12:00:00'), Timestamp('2019-11-02 15:00:00'), Timestamp('2019-11-02 18:00:00'), Timestamp('2019-11-02 21:00:00'), Timestamp('2019-11-03 00:00:00'), Timestamp('2019-11-03 02:42:00')]

 2019.307    , 2019-11-02 21:18:00 ,  2019-11-04 02:42:00 , 29.4

 2019.308    , 2019-11-03 21:18:00 ,  2019-11-05 02:42:00 , 29.4

 2019.309    , 2019-11-04 21:18:00 ,  2019-11-06 02:42:00 , 29.4

 2019.310    , 2019-11-05 21

Loaded data from pickle...  2019 feb msis2
y_num month 2019 mar


Loaded data from pickle...  2019 mar msis2
y_num month 2019 apr


Loaded data from pickle...  2019 apr msis2
y_num month 2019 may


Loaded data from pickle...  2019 may msis2
y_num month 2019 jun


Loaded data from pickle...  2019 jun msis2
y_num month 2019 jul


Loaded data from pickle...  2019 jul msis2
y_num month 2019 aug


Loaded data from pickle...  2019 aug msis2
y_num month 2019 sep


Loaded data from pickle...  2019 sep msis2
y_num month 2019 oct


Loaded data from pickle...  2019 oct msis2
y_num month 2019 nov


Loaded data from pickle...  2019 nov msis2
y_num month 2019 dec


Loaded data from pickle...  2019 dec msis2
y_num month 2019 jan


Loaded data from pickle...  2019 jan jb2008
y_num month 2019 feb


Loaded data from pickle...  2019 feb jb2008
y_num month 2019 mar


Loaded data from pickle...  2019 mar jb2008
y_num month 2019 apr


Loaded data from pickle...  2019 apr jb2008
y_num month 2019 may


Loaded

0

## plot settings

In [5]:
def plot_cleanformat_axes(fig, font_dict):
    rownum, colnum = fig._get_subplot_rows_columns()

    for i in rownum:
        if len(rownum)==1:
            L_ticklabel = True
        else:
            if i < len(rownum):
                L_ticklabel = False
            else:
                L_ticklabel = True
        fig.update_xaxes(### LINE at axis border
                          showline=True,
                          showticklabels=L_ticklabel,
    #                       tickformat= '%m/%d',
                          linecolor='black',
                          linewidth=1,
                         ### Major ticks
                          ticks='inside',
                          tickfont=font_dict,
                          mirror=True,
    #                       tickwidth=2,
    #                       ticklen=9,
                          tickcolor='grey',
    #                       tick0="2018-11-9" ,
    #                       dtick=86400000.0*1,    # milliseconds in a day, every 7 days
                          #### Minor Ticks
                           minor=dict(
                             dtick=86400000.0, # milliseconds in a day
                             tickwidth=1,
                             ticklen=4,
                             tickcolor='grey',
                             ticks='inside'),
                          ### GRID
                           gridcolor='gainsboro',
                           gridwidth=1,
                           layer='above traces',
                           tickangle=0,
                           row=i, col=1)
        fig.update_yaxes(showline=True,      # add line at x=0
                             showticklabels=True,
                             linecolor='black',  # line color
                             linewidth=1,        # line size
                         ticks='inside',     # ticks outside axis
                         tickfont=font_dict, # tick label font
                         mirror='allticks',  # add ticks to top/right axes
                         tickwidth=1,      # tick width
                         tickcolor='black',  # tick color
                         gridcolor='gainsboro',
                         gridwidth=1,
                         layer='above traces',
                         row=i, col=1)
    return(fig)

from pygeodyn.pygeodyn_plot_scalingfactors import *

coldict = {}
coldict['msis2']     = "#2ca02c"  # 'tab:green'
coldict['dtm2020_o'] = "#d62728"  # 'tab:red'
coldict['jb2008']    = "orange"   
coldict['hasdm_oc']  = "#1f77b4"     


# Scaling Factors, Scaled Densities, Weighted Average Density

In [6]:
  
satid = 1807001
wgts = {}

for model in run_dict.keys():
    wgts[model] = {}
    ScalingFactors  = []
    ScalingFactor_times = []

    for ii,arc in enumerate(obj[model]['global_params']['arc_input']):
        if arc == '2019.365':
            continue
        
        epochstart = obj[model]['global_params']['prms']['epoch_start'][ii]
        hrs = pd.to_datetime(epochstart, format='%Y-%m-%d %H:%M:%S').hour
        frachours =(hrs/24)
        #
        if len(arc) == 9:
            maneuv_indicator = arc[8]
        else:
            maneuv_indicator = ''
        arc_type = obj[model]['global_params']['prms']['arc_type']
        if arc_type == "Nominal30hr_and_AB":
            arc_name =arc[:8]+ maneuv_indicator
            arc_name_DOY = arc[:8]
        else:
            arc_name =arc[:8]+('%.3f'%frachours).lstrip('0')+ maneuv_indicator
        ### Collect the weights for the ensemble average
        inv_rms          = 1/obj[model]['Statistics'][arc_name]['T_RMS'].values[0]
        wgts[model][arc_name_DOY] = inv_rms#/sum_wgts

        iters = int(obj[model]['run_parameters'+arc_name]['total_iterations']) 
        for iit, itime in enumerate(obj[model]['AdjustedParams'][arc_name][iters][satid]['0CD'].keys()):
            
            numSFs = len(obj[model]['AdjustedParams'][arc_name][iters][satid]['0CD'])
            
            if iit == 0 or iit==numSFs-1:   # remove the first and last Scaling Factor to account for edge effects
                pass
            else:
                CURRENT_VALUE = obj[model]['AdjustedParams'][arc_name][iters][satid]['0CD'][itime]['CURRENT_VALUE']
                APRIORI_VALUE = obj[model]['AdjustedParams'][arc_name][iters][satid]['0CD'][itime]['APRIORI_VALUE']
                ScalingFactors.append(CURRENT_VALUE/APRIORI_VALUE)
                ScalingFactor_times.append(itime)
    run_dict[model]['ScalingFactor_times'] = ScalingFactor_times
    run_dict[model]['ScalingFactors']      = ScalingFactors
    run_dict[model]['Weight'] = wgts[model]
    

    
###### SCALE THE DENSITIES:
models_dens = {}
for monthmodel in run_dict.keys():
    print(f"---Making continuous scaled rho for {monthmodel}")
    models_dens[monthmodel] = get_continuous_scaled_densities(obj, run_dict, monthmodel, scale_cadence)

    del obj[monthmodel]
    gc_collect()

del obj
gc_collect()

# Retrieve scaled ensemble weighted average
#     'Rho_x' denotes the ensemble weighted avg
print(f"")
print(f"--- Processing Rho_x")
yearmonth_list = [
                  '2019jan',
                  '2019feb',
                  '2019mar',
                  '2019apr',
                  '2019may',
                  '2019jun',
                  '2019jul',
                  '2019aug',
                  '2019sep',
                  '2019oct',
                  '2019nov',
                  '2019dec',
                 ]

models_dens =  calc_rho_ScaledEnsembleWgtAvg(models_dens, run_dict, yearmonth_list, run_list)




---Making continuous scaled rho for 2018octmsis2
---Making continuous scaled rho for 2018novmsis2
---Making continuous scaled rho for 2018decmsis2
---Making continuous scaled rho for 2019janmsis2
---Making continuous scaled rho for 2019febmsis2
---Making continuous scaled rho for 2019marmsis2
---Making continuous scaled rho for 2019aprmsis2
---Making continuous scaled rho for 2019maymsis2
---Making continuous scaled rho for 2019junmsis2
---Making continuous scaled rho for 2019julmsis2
---Making continuous scaled rho for 2019augmsis2
---Making continuous scaled rho for 2019sepmsis2
---Making continuous scaled rho for 2019octmsis2
---Making continuous scaled rho for 2019novmsis2
---Making continuous scaled rho for 2019decmsis2
---Making continuous scaled rho for 2018octjb2008
---Making continuous scaled rho for 2018novjb2008
---Making continuous scaled rho for 2018decjb2008
---Making continuous scaled rho for 2019janjb2008
---Making continuous scaled rho for 2019febjb2008
---Making conti

## Load Flux, Kp from gdntable.data

In [7]:
import linecache
import pandas as pd
import numpy as np

path_to_flux = "/data/SatDragModelValidation/src/geodyn_code/support/geodyn_support/make_tables/"


dateS   = []
dateAP  = []
dateKP8 = []

fluxS   = []
fluxAP  = []
fluxKP8 = []

switch = 0
with open(path_to_flux+"new_master", 'r') as f:
    for line_no, string in enumerate(f):
#         string = linecache.getline("new_master",line+1) #

        if 'MASTER' in string:        
            switch = 'skip'
            continue
            
        ### Skip the title lines and any dates before Y2K
        if 'FLUXS' in string:        
            switch = 'readfluxS'
            print(switch)
            continue

        if 'FLUXAP' in string:        
            switch = 'readfluxAP'
            print(switch)
            continue
        if 'FLUXKP8' in string:        
            switch = 'readfluxKP8'
            print(switch)
            continue

        if switch =='skip':
            continue
            
        if int(string[:2]) >= 58:
            continue
        else:
            
            if int(string[:2]) < 18 or int(string[:2]) > 19:
                continue
                
            if switch == 'readfluxS':
                ### Load the Solar Flux values after 2000. The date leading each line represents
                ### the first flux value in that line.  The following n values are that day + n days.
                ###  All Solar Flux values are mulitplied by 10 for some reason...

                for n in range(0,12):
                    dateS.append(pd.to_datetime(string[:6],format='%y%m%d') + n*pd.to_timedelta(1,'d') )
                fluxS.append(int(string[11:15]) / 10)
                fluxS.append(int(string[16:20]) / 10)
                fluxS.append(int(string[21:25]) / 10)
                fluxS.append(int(string[26:30]) / 10)
                fluxS.append(int(string[31:35]) / 10)
                fluxS.append(int(string[36:40]) / 10)
                fluxS.append(int(string[41:45]) / 10)
                fluxS.append(int(string[46:50]) / 10)
                fluxS.append(int(string[51:55]) / 10)
                fluxS.append(int(string[56:60]) / 10)
                fluxS.append(int(string[61:65]) / 10)
                fluxS.append(int(string[66:70]) / 10)

            if switch == 'readfluxAP':
                ### Load the AP values after 2000. These are formatted the same as the FLUXS section
                for n in range(0,12):
                    dateAP.append(pd.to_datetime(string[:6],format='%y%m%d') + n*pd.to_timedelta(1,'d') )
                fluxAP.append(int(string[11:15]) / 10)
                fluxAP.append(int(string[16:20]) / 10)
                fluxAP.append(int(string[21:25]) / 10)
                fluxAP.append(int(string[26:30]) / 10)
                fluxAP.append(int(string[31:35]) / 10)
                fluxAP.append(int(string[36:40]) / 10)
                fluxAP.append(int(string[41:45]) / 10)
                fluxAP.append(int(string[46:50]) / 10)
                fluxAP.append(int(string[51:55]) / 10)
                fluxAP.append(int(string[56:60]) / 10)
                fluxAP.append(int(string[61:65]) / 10)
                fluxAP.append(int(string[66:70]) / 10)

            if switch == 'readfluxKP8':
                ### Load the KP values after 2000. These are formatted such that each line is a day
                ### and each nth value in the line is n*3hrs for the day
                for n in range(0,8):
                    dateKP8.append(pd.to_datetime(string[:6],format='%y%m%d') + n*pd.to_timedelta(3,'h') )
                fluxKP8.append(int(string[7:11])  / 100)
                fluxKP8.append(int(string[12:16]) / 100)
                fluxKP8.append(int(string[17:21]) / 100)
                fluxKP8.append(int(string[22:26]) / 100)
                fluxKP8.append(int(string[27:31]) / 100)
                fluxKP8.append(int(string[32:36]) / 100)
                fluxKP8.append(int(string[37:41]) / 100)
                fluxKP8.append(int(string[42:46]) / 100)

fluxS = np.array(fluxS)
fluxAP = np.array(fluxAP)
fluxKP8 = np.array(fluxKP8)
                
fluxS   = np.where(fluxS  == 0., np.nan, fluxS  )
fluxAP  = np.where(fluxAP ==0., np.nan, fluxAP )
fluxKP8 = np.where(fluxKP8==0., np.nan, fluxKP8)



readfluxS
readfluxAP
readfluxKP8


# Plot

In [9]:
%load_ext autoreload
%autoreload 2


def PLOT_resids(fig,  den_dict, model_dict, _model_name_):
    
    SHOW_alldata = True
    
    model_m1 = _model_name_[7:]
#     print('model_m1', model_m1)

    fig.add_trace(go.Scattergl(x=pd.to_datetime(model_dict['ScalingFactor_times'])-pd.to_timedelta(scale_cadence/2, 'h'),
                           y=model_dict['ScalingFactors'],
                           name= model,
                           mode='markers',
                           opacity=1,
                           marker=dict(color=coldict[model_m1], size=5),
#                                marker=dict(color=coldict[model_m1], 
#                                            size=6,
#                                            symbol='line-ew',
#                                            line = dict(color = coldict[model_m1], width=3)), #symbol='diamond-wide'),
#                            line = dict(shape = 'hvh',dash ='dash', color = coldict[model_m1], width=1),
                           showlegend=False),
                           secondary_y=False,row=2, col=1)

    
    
    time_avg,dscale_avg = orbit_avg_generic(den_dict['dates'], den_dict['denscaled'], den_dict['lat'])
    ## -----------------------------------------------------------------------------------------------------
    ##     Orbit Averaged Density
    fig.add_trace(go.Scattergl(x=time_avg,
                               y=dscale_avg,
                               ### name= model_m1,
                               mode='markers+lines',
                               opacity=1,
                                   marker=dict(color=coldict[model_m1],size=2),
                                   line = dict(dash ='solid', color = coldict[model_m1], width=2),
                               showlegend=False), row=4, col=1)
#     fig.add_trace(go.Scattergl(x=den_dict['dates'],
#                                y=den_dict['denscaled'],
#                                ### name= model_m1,
#                                mode='markers+lines',
#                                opacity=1,
#                                    marker=dict(color=coldict[model_m1],size=2),
#                                    line = dict(dash ='solid', color = coldict[model_m1], width=2),
#                                showlegend=False), row=3, col=1)

    
    
    
    
    time_avg,d_avg = orbit_avg_generic(den_dict['dates'], den_dict['dens'], den_dict['lat'])
    ### -----------------------------------------------------------------------------------------------------
    ###     Orbit Averaged Density
#     fig.add_trace(go.Scattergl(x=den_dict['dates'], #time_avg,
#                                y=den_dict['dens'], #d_avg,
#                                ### name= model_m1,
#                                mode='markers+lines',
#                                opacity=1,
#                                    marker=dict(color=coldict[model_m1],size=1),
#                                    line = dict(dash ='solid', color = coldict[model_m1], width=2),
#                                showlegend=False), row=2, col=1)

    ###     Orbit Averaged Density
    fig.add_trace(go.Scattergl(x=time_avg,
                               y=d_avg,
                               ### name= model_m1,
                               mode='markers+lines',
                               opacity=1,
                                   marker=dict(color= coldict[model_m1],size=2),
                                   line = dict(dash ='solid', color = coldict[model_m1], width=2),
                               showlegend=False), row=3, col=1)
    
    
#                 time_avg,CD_avg, area_avg_rolling, CD_std = orb_avg_param(obj_m1.__dict__['DragFile'], arc_string, 'TOTAREA')
#                 fig.add_trace(go.Scattergl(x=time_avg,
#                                            y=area_avg_rolling,
#     #                                          name= plot_name+arc,
#                                              mode='markers+lines',
#                                              opacity=1,
#                                              marker=dict(color=col,size=2,),
#                                              line = dict(shape='hvh', dash ='solid', color = col, width=3),
#                                              showlegend=False, ),
#                                              secondary_y=False,
#                                              row=3, col=1,
#                                          )

    return(fig)


fig  = make_subplots(
    rows=4, cols=1,
    vertical_spacing = 0.05,
    shared_xaxes=True)


fig = make_subplots(rows=4, cols=1, row_heights=[0.1, 0.3, 0.3, 0.3],#],
                    specs=[[{"secondary_y": True}],
                           [{"secondary_y": False}],
                           [{"secondary_y": False}],
                           [{"secondary_y": False}]],
                           shared_xaxes=True,
                           vertical_spacing=0.02)




fig.add_trace(go.Scattergl(x=dateS,
                           y=fluxS,
                           name= 'F107d_1AU',
                           mode='lines',
                           opacity=1,
                           line = dict(shape = 'hvh',dash='dash', color = 'blue', width=2),
                           showlegend=False),
                           secondary_y=True,row=1, col=1)

fig.add_trace(go.Scattergl(x=dateKP8,
                           y=fluxKP8,
                           name= 'Kp',
                           mode='lines',
                           opacity=1,
                           line = dict(shape = 'hvh', color = 'black', width=2),
                           showlegend=False),
                           secondary_y=False,row=1, col=1) 

fig.update_yaxes(title_text="Kp", 
                 exponentformat= 'power',
#                  range=[0,7],
                 secondary_y=False,
                 row=1, col=1)
fig.update_yaxes(title_text="F10.7", 
                 exponentformat= 'power',
                 range=[35,170],
                 secondary_y=True,
                 tickfont=dict(color="blue"),
                 titlefont=dict(color="blue"),
                 row=1, col=1)

for model in run_dict.keys():
#     for imonth,month in enumerate(month_list):
#     print('model', model)

    fig = PLOT_resids(fig, models_dens[model], run_dict[model], model)

    
#######################################################
font_dict=dict(family='Arial',size=11,color='black')
## automate the specification of the axes for subplots
rownum, colnum = fig._get_subplot_rows_columns()
for i in rownum:
    if len(rownum)==1:
        L_ticklabel = True
    else:
        if i < len(rownum):
            L_ticklabel = True
        else:
            L_ticklabel = True
    fig.update_xaxes(### LINE at axis border
                      showline=True,
                      showticklabels=L_ticklabel,
#                       tickformat= '%m/%d',
                      linecolor='black',
                      linewidth=1,
                     ### Major ticks
                      ticks='inside',
                      tickfont=font_dict,
                      mirror=True,
#                       tickwidth=2,
#                       ticklen=9,
                      tickcolor='grey',
#                       tick0="2018-11-9" ,
#                       dtick=86400000.0*1,    # milliseconds in a day, every 7 days
                      #### Minor Ticks
                       minor=dict(
                         dtick=86400000.0, # milliseconds in a day
                         tickwidth=1,
                         ticklen=4,
                         tickcolor='grey',
                         ticks='inside'),
                      ### GRID
                       gridcolor='gainsboro',
                       gridwidth=1,
                       layer='above traces',
                       tickangle=0,
                       row=i, col=1)
    fig.update_yaxes(showline=True,      # add line at x=0
                         showticklabels=True,
                         linecolor='black',  # line color
                         linewidth=1,        # line size
                     ticks='inside',     # ticks outside axis
                     tickfont=font_dict, # tick label font
                     mirror='allticks',  # add ticks to top/right axes
                     tickwidth=1,      # tick width
                     tickcolor='black',  # tick color
                     gridcolor='gainsboro',
                     gridwidth=1,
                     layer='above traces',
                     row=i, col=1)

    fig.update_yaxes(title_text="Scaling Factor", 
                     exponentformat= 'power',row=2, col=1)

    fig.update_yaxes(title_text="Density", 
                     type="log", 
                     exponentformat= 'power',row=3, col=1)
    fig.update_yaxes(title_text="Scaled Density", 
                      type="log", 
                     exponentformat= 'power',row=4, col=1)

# for month in yearmonth_list:

#     time_avg,Rho_x = orbit_avg_generic(models_dens[month+'Rho_x']['date'],
#                                             models_dens[month+'Rho_x']['Rho_x'],
#                                             models_dens[month+'Rho_x']['lat'])

#     time_avg,Rho_std = orbit_avg_generic(models_dens[month+'Rho_x']['date'],
#                                             models_dens[month+'Rho_x']['Rho_std'],
#                                             models_dens[month+'Rho_x']['lat'])


#     fig.add_trace(go.Scattergl(x=time_avg,
#                                y=Rho_x,
#                                ### name= model_m1,
#                                mode='markers+lines',
#                                opacity=1,
#                                marker=dict(color='black',size=5),
#                                    line = dict( dash ='solid', color = 'black', width=4),
#                                showlegend=False), row=4, col=1)
    ## ERRROR BARS
#     fig.add_trace(go.Scattergl(x=time_avg,
#                                y=np.array(Rho_x)\
#                                    +np.array(Rho_std),
#                                ### name= model_m1,
#                                mode='lines',
#                                opacity=.8,
#                                    line = dict( dash ='dash', color = 'grey', width=3),
#                                showlegend=False), row=4, col=1)
#     fig.add_trace(go.Scattergl(x=time_avg,
#                                y=np.array(Rho_x)\
#                                   -np.array(Rho_std),
#                                ### name= model_m1,
#                                mode='lines',
#                                opacity=.8,
#                                    line = dict( dash ='dash', color = 'grey', width=3),
#                                showlegend=False), row=4, col=1)

    
fig.update_xaxes(range=[pd.to_datetime('2018-10-14 00:00:00'), pd.to_datetime('2019-12-31 00:00:00')])
    
a='input'
s=settings_ice
fig.update_layout(title=f" ICESat-2 {s['cd_model'][a]}, {s['hours_between_cd_adj'][a]}-hr Scale", 
                  autosize=False,    width=850,    height=900,
                  legend= {'itemsizing': 'trace'},
                  font=font_dict,
                  plot_bgcolor='white', 
                 )
fig.update_annotations(font_size=16)  # Increase size of subplot title



# fig.add_vline(x=datetime.strptime("2019-06-20 00:00", "%Y-%m-%d %H:%M").timestamp() * 1000,                
# #                             annotation_text="Sailboat (-B)", 
#                             annotation_position="top right",
#                             annotation_font_size=12,
#                             annotation_font_color="#FC1CBF",
#                             line_width=2, line_dash="dash",
# #                           row=3, col=1)
#                          )


# fig.add_vline(x=datetime.strptime("2019-09-06 20:00", "%Y-%m-%d %H:%M").timestamp() * 1000,                
# #                             annotation_text="Sailboat (-B)", 
#                             annotation_position="top right",
#                             annotation_font_size=12,
#                             annotation_font_color="#FC1CBF",
#                             line_width=2, line_dash="dash",
# #                           row=3, col=1)
#                          )

# fig.show(config=config)
fig.show(config= dict({
                'displayModeBar': False,
                'responsive': True,
                'staticPlot': False,
                'displaylogo': False,
                'showTips': False,
                }),
#          renderer='jpg',
)




The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
